In [4]:
import os
import folium
import pandas as pd
import numpy as np
import networkx as nx
from haversine import haversine

In [5]:
nodes = pd.read_csv('data/Jeju_nodes.csv', encoding='utf-8')
links = pd.read_csv('data/Jeju_links.csv', encoding='cp949')
car = pd.read_csv('data/Jeju_car.csv', encoding='cp949')

nodes = nodes[['Id','NODE_NAME','latitude','longitude']]
links = links[['Source','Target', '시간']]
source_in = links['Source'].apply(lambda x : x in list(nodes['Id'])) # check Sources are in jeju
target_in = links['Target'].apply(lambda x : x in list(nodes['Id'])) # check Targets are in jeju
# source_in and target_in are boolean type pandas.Series which contains True or False
jeju_links = links[source_in & target_in] # contain if both target and source are contained in jeju

In [6]:
G = nx.Graph()
# R is the Earth's radius
R = 6371e3

for idx,row in nodes.iterrows():
    # add node to Graph G
    G.add_node(row['Id'],Label=row['NODE_NAME'],latitude=row['latitude'], longitude=row['longitude'])

for idx,row in jeju_links.iterrows():
    # Link attribute : 'Source', 'Target' and weight = '시간 between two nodes'
    G.add_edge(row['Source'],row['Target'],weight = row['시간'])

In [7]:
len(G.nodes)

4218

In [8]:
def connectRes(graph, df): 
    nodes_latitude = nx.get_node_attributes(graph, 'latitude')
    nodes_longitude = nx.get_node_attributes(graph, 'longitude')
    for idx, row in df.iterrows():
        distances ={}
        for keyLong, valLat in nodes_latitude.items():
            nodesPos = (valLat, nodes_longitude[keyLong])
            curPos = (row['latitude'], row['longitude'])
            distances[keyLong] = haversine(nodesPos, curPos, unit='km')
        nearest_node = min(distances, key=distances.get)
        graph.add_node(idx, Label=idx, latitude=row['latitude'], longitude=row['longitude'])
        w = distances[nearest_node]*1000/666 
        graph.add_edge(nearest_node, idx, weight=w) 
    return graph

G = connectRes(G, car)
print(f"Data: {len(car)}, Nodes: {len(G.nodes)}, Edges: {len(G.edges)}")

Data: 26, Nodes: 4244, Edges: 6041


In [9]:
def propagation(G, start_node, w = 5):
    shortest_paths = nx.single_source_dijkstra_path_length(G, start_node, cutoff=w, weight='weight')
    # print(f"Start node: {start_node}")
    # print(f"Number of selected Node: {len(shortest_paths)}")
    return shortest_paths

def mergeDict(dict1, dict2):
    result_dict = {}

# Iterate over keys present in both dictionaries
    for key in set(dict1.keys()).intersection(dict2.keys()):
        # Choose the smaller value
        result_dict[key] = min(dict1[key], dict2[key])

    # Add keys from the first dictionary that are not in the second dictionary
    result_dict.update({key: dict1[key] for key in set(dict1.keys()) - set(dict2.keys())})

    # Add keys from the second dictionary that are not in the first dictionary
    result_dict.update({key: dict2[key] for key in set(dict2.keys()) - set(dict1.keys())})

    return result_dict

serviceArea = {}
for idx, row in car.iterrows():
    tmp = propagation(G, idx, w=5)
    serviceArea = mergeDict(serviceArea, tmp)

print(serviceArea)


{0: 0, 1: 0, 2: 0, 3: 0, 4050026500.0: 0.6671108712575287, 4: 0, 6: 0, 5: 0, 7: 0, 9: 0, 10: 0, 11: 0, 12: 0, 13: 0, 8: 0, 14: 0, 16: 0, 17: 0, 18: 0, 19: 0, 4050042900.0: 2.9602772982510963, 20: 0, 22: 0, 23: 0, 4060184600.0: 3.2900091120745127, 21: 0, 24: 0, 4060086300.0: 2.6406080111745127, 4050051100.0: 2.089132427764488, 4050059300.0: 2.868875030632025, 4050059301.0: 2.994829668532025, 4050067500.0: 1.9675812295320247, 4050067501.0: 1.332803618532025, 4050067502.0: 1.7536025755320248, 4060102700.0: 0.17531371594703724, 4060004400.0: 3.6050272670774848, 4060004401.0: 3.7792613220774847, 4060004402.0: 3.8149631974774847, 4060004403.0: 3.5688272445774847, 4050075700.0: 1.1391083936939204, 4060004404.0: 3.4114124260774847, 4050075701.0: 1.4303209686939202, 4060004405.0: 3.937086201577485, 4050182200.0: 4.063177383616736, 4050075702.0: 1.9133999896939202, 4060004406.0: 3.452430303277485, 4050083900.0: 3.003939363557529, 4050092100.0: 1.7034045731644878, 4060029000.0: 1.507830483829926,

도로망 + 현재 119 center위치 시각화

In [10]:
# Center of Jeju
std_point = (33.37283976160554, 126.4439861097205 )

In [11]:
map_osm = folium.Map(location=std_point, zoom_start=10) 

kw = {'opacity': 0.5, 'weight': 2}
for edge in G.edges(data=True):
    source, target, attributes = edge

    # Check if the source and target nodes exist in the graph
    if source in G.nodes and target in G.nodes:
        start = tuple([G.nodes[source]['latitude'], G.nodes[source]['longitude']])
        end = tuple([G.nodes[target]['latitude'], G.nodes[target]['longitude']])

        folium.PolyLine(
            locations=[start, end],
            color='blue',
            line_cap='round',
            **kw,
        ).add_to(map_osm)
    else:
        print(source, target)

# for key, val in serviceArea.items():
#     row = nodes.loc[nodes['Id'] == key]
#     try:
#         location = (row['latitude'].values[0], row['longitude'].values[0]) 
#     except:
#         # print(row, key)
#         pass

#     folium.Circle(
#         location=location,
#         radius=500, 
#         color='white',
#         weight=1,
#         fill_opacity=0.6,
#         opacity=1,
#         fill_color='red',
#         fill=True,  # gets overridden by fill_color
#         # popup=str(row['Id'])
#     ).add_to(map_osm)

for ix, row in car.iterrows():
    location = (row['latitude'], row['longitude']) 
    folium.Circle(
        location=location,
        radius=1000, 
        color='white',
        weight=1,
        fill_opacity=0.6,
        opacity=1,
        fill_color='black',
        fill=True,  # gets overridden by fill_color
        # popup=str(row['Id'])
    ).add_to(map_osm)

map_osm